# Diagonalisering af symmetriske matricer

Demo af Christian Mikkelstrup og Hans Henrik Hermansen

In [ ]:
from sympy import *
init_printing()

I den sidste demo diagonaliserede vi en symmetrisk matrix ved at lave alle steps ind imellem. Dog er alle steps præcis de samme, uanset hvilken symmetrisk matrix man får! Det er derfor muligt at lave en funktion (vores, og altså ikke en indbygget) som kan give både $Q$ og $\Lambda$ som opfylder,

\begin{equation}
Q^\top\, A\, Q = \Lambda.
\end{equation}

Der er tilføjet et par ekstra tjek således at den giver en god fejlbesked, hvis den bruges på matricer som den ikke burde bruges på! Dette skal lige så meget bruges som et eksempel på hvordan man sagtens kan bygge sine egne funktioner der regner matematik ved brug af Python og SymPy!

In [ ]:
def orto_diag_symmetrisk(A, numeric=False):
    """
    Inputs:
        A: Matrix()
            Symmetrisk matrix af størrelse (n x n)
        numeric: Bool
            True/False, om der skal regnes numerisk (hurtigere)
            
    Output:
        (Q, Lamda)
            Q og Lamda matricer der opfylder Q.T*A*Q = Lamda
            Q er positiv ortogonal og Lamda er diagonal
    """
    
    # Finder ud af om korrekt matrix er input
    assert type(A) == type(Matrix([])), "Fejl: Input var ikke en matrix!"
    assert A.shape[0] == A.shape[1], "Fejl: Matricen er ikke kvadratisk!"
    assert A.T == A, "Fejl: Matricen givet er ikke symmetrisk!"
    assert A.rank() == A.shape[0], "Fejl: Matricen har ikke fuld rank. \
        Det er derfor ikke muligt at finde nok lineært uafhængige vektorer!"
    
    # Nu finder vi egenvektorer
    U, Lamda = A.diagonalize()
    u_list = [U.col(k) for k in range(A.shape[0])]
    
    if(numeric):
        # evaluate as floating (evalf)
        u_list = [u.evalf() for u in u_list]
        
    v_list = GramSchmidt(u_list, orthonormal=True)
    Q = Matrix.hstack(*v_list)
    
    # Numeriske problemer for nogle matricer. Tjekker imaginærdelen af tallet
    assert im(det(Q)) < 1e-15, "Fejl: Determinanten af Q var forventet til \
                               enten 1 eller -1, men imaginær del blev fundet!"
    
    # Hvis negativ ortogonal
    if(re(det(Q)) < 0):
        v_list[0] = -v_list[0]
        Q = Matrix.hstack(*v_list)
        
    return Q, Lamda

Denne funktion burde altså virke på alle matricer! Vi kan jo lige prøve på matricen fra sidste uges demo:

In [ ]:
A = Matrix([[6,2,4],[2,9,-2],[4,-2,6]])
A
U, Lamda = A.diagonalize()
u_list = [U.col(k) for k in range(A.shape[0])]
u_list

In [ ]:
Q, Lambda = orto_diag_symmetrisk(A)
Q, Lambda

Som eftertjekkes ved

In [ ]:
Q.T*A*Q, Q*Q.T

Dette virker også med større matricer,

In [ ]:
B = Matrix([[0,1,1,-1],[1,0,-1,1],[1,-1,0,1],[-1,1,1,0]])
B

In [ ]:
Q, Lambda = orto_diag_symmetrisk(B)
Q, Lambda

Som eftertjekkes ved

In [ ]:
Q.T*B*Q

Denne metode skal dog ikke bruges hovedløst! Den finder ikke frem til et svar inden for tiden af min tålmodighed, hvis man giver den følgende matrix:

In [ ]:
C = Matrix([[1,1,0],[1,0,1],[0,1,0]])
C
# orto_diag_symmetrisk(C)

Dog kan man komme i mål med en numerisk løsning ved

In [ ]:
Q, Lamda = orto_diag_symmetrisk(C, numeric=True)
Q, Lamda

Bemærk at $Q$ nu kun er approksimativt ortogonal:

In [ ]:
N(Q.T * Q)

Eller vi kan tænke os endnu mere om. Den symmetriske matrix har nemlig 3 forskellige egenværdier:

In [ ]:
eigs = C.eigenvals(multiple=True)
display(eigs)           # eksakte egenværdier
[N(ev) for ev in eigs]  # decimaltal approx

De tre egenvektorer hørende til disse tre egenværdier er derfor alle allerede ortogonale, og vi behøver kun normalisere dem:

In [ ]:
v1, v2, v3 = tuple([vec[2][0].normalized() for vec in C.eigenvects()])   # virker kun når gm=1
V = Matrix.hstack(-v1,v2,v3)
V
# I en samlet kommando:
# C.diagonalize(normalize=True)

Kapow, SymPy kastede matematik ud på flere A4-sider! Det er defor dog nok alligevel mere nyttigt med den numeriske approksimation, som vi kan genfinde ved:

In [ ]:
N(V)

De fundne $Q$ og $V$ stemmer godt overens:

In [ ]:
N(V-Q)